# AE4350 - Bio-inspired Intelligence and Learning Assignment

This is the Main script describing the DRL portfolio management system
<br>Created on Thu May 12 13:22:50 2022
<br>@author: Reinier Vos, 4663160-TUD

In [1]:
from utility_v2 import Agent, getStockData, getState, formatPrice
import sys
from tqdm import tqdm # gives progress bar when loading
import os
#In TensorFlow 2.3+, you can disable eager mode anytime using the following method:
import tensorflow as tf
tf.config.run_functions_eagerly(True)
#tf.config.run_functions_eagerly(False)


In [2]:
window_size = 100
batch_size = 32
checkpoint_dir = "run1"
agent = Agent(window_size, batch_size,checkpoint_dir)
data = getStockData("traindata")
l = len(data) - 1

episode_count = 300

C:\Users\Reinier Vos\anaconda3\envs\tf-gpu\lib\site-packages\keras\optimizer_v2\adam.py:105: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)


In [3]:
printTrades = False

pbar = tqdm(total=l*episode_count, position=0, leave=True, bar_format='{l_bar}{bar}| {n_fmt}/{total_fmt} ') # progress bar
total_profit_list = []
EveryProfit_dct = {}
for e in range(episode_count):
    #print("== Episode " + str(e) + "/" + str(episode_count) +" ==")
    state = getState(data, 0, window_size + 1)

    agent.inventory = []
    total_profit = 0 # total profit resets every epsiode 
    prev_reward = 0 
    profits = []
    done = False
    for t in range(l):
        action = agent.act(state)
        
        action_prob = agent.actor_local.model.predict(state)

        next_state = getState(data, t + 1, window_size + 1)
        reward = 0

        if action == 1:
            agent.inventory.append(data[t])
            if printTrades:
                print("Buy:" + formatPrice(data[t]))

        elif action == 2 and len(agent.inventory) > 0:
            bought_price = agent.inventory.pop(0)
            reward = max(data[t] - bought_price, 0)
            total_profit += data[t] - bought_price
            if printTrades:
                print("sell: " + formatPrice(data[t]) + "| profit: " + formatPrice(data[t] - bought_price))
            prev_reward = data[t] - bought_price
            profits.append(prev_reward)

        if t == l - 1:
            done = True
        agent.step(action_prob, reward, next_state, done)
        state = next_state
        '''
        if done:
            print("------------------------------------------")
            print("Total Profit: " + formatPrice(total_profit))
            print("------------------------------------------")
        '''
        pbar.set_description("Training profit for step {}/{} of episode {}| previous profit {} & total profit {}" % (int(t),int(l), int(e),float(prev_reward),float(total_profit)))
        pbar.update()
        
    # collect & save
    total_profit_list.append(total_profit)
    EveryProfit_dct["e{}".format(e)] = profits

C:\Users\Reinier Vos\AppData\Roaming\Python\Python37\site-packages\tensorflow\python\data\ops\structured_function.py:265: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  "Even though the `tf.config.experimental_run_functions_eagerly` "


Episode 0/300
Buy:$2067.91
Buy:$2095.27
sell: $2087.31| profit: $19.40
sell: $2102.07| profit: $6.80
Buy:$2077.09
Buy:$2123.66
Buy:$2102.49
Buy:$2098.18
Buy:$2080.03
Buy:$2052.74
Buy:$2049.73
Buy:$2044.66
Buy:$2071.02
Buy:$2095.38
sell: $2101.78| profit: $24.69


C:\Users\Reinier Vos\Documents\YEAR2021_2022\AE MSc C&S\AE4350-Bio_inspiredIntelligenceAndLearning\assignment\scripts\utility_v2.py:246: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  local_weights = np.array(local_model.get_weights())
C:\Users\Reinier Vos\Documents\YEAR2021_2022\AE MSc C&S\AE4350-Bio_inspiredIntelligenceAndLearning\assignment\scripts\utility_v2.py:247: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  target_weights = np.array(target_model.get_weights())


Buy:$2119.89
Buy:$2112.50
Buy:$2109.45
sell: $2082.10| profit: -$41.56
Buy:$2091.33
sell: $2081.12| profit: -$21.37
sell: $2093.23| profit: -$4.95
Buy:$2102.54
Buy:$2104.89
Buy:$2112.86
sell: $2122.95| profit: $42.92
sell: $2124.50| profit: $71.76
Buy:$2120.01
Buy:$2100.43
Buy:$2096.04
Buy:$2104.58
sell: $2092.13| profit: $42.40
Buy:$2110.23
sell: $2087.38| profit: $42.72
sell: $2077.59| profit: $6.57
Buy:$2112.80
Buy:$2103.19
sell: $2094.38| profit: -$1.00
Buy:$2072.37
Buy:$2091.51
Buy:$2056.52
Buy:$2064.11
Buy:$2052.96
Buy:$2045.50
sell: $2090.32| profit: -$29.57
Buy:$2061.23
Buy:$2039.69
Buy:$2044.16
Buy:$2072.21
Buy:$2067.27
Buy:$2095.22
Buy:$2103.75
sell: $2103.00| profit: -$9.50
Buy:$2085.44
sell: $2090.79| profit: -$18.66
Buy:$2092.15
Buy:$2086.70
sell: $2069.98| profit: -$21.35
sell: $2048.62| profit: -$53.92
sell: $2022.71| profit: -$82.18
sell: $1980.90| profit: -$131.96
sell: $1993.38| profit: -$126.63
sell: $1989.18| profit: -$111.25
Buy:$2001.49
sell: $2019.91| profit: -$7

KeyboardInterrupt: 

import os
checkpoint_path = "run1"
os.mkdir(os.path.join(checkpoint_path,"e{}".format(e)))
agent.actor_local.model.save_weights(os.path.join(checkpoint_path,"e{}".format(e), 'actor_local.h5'))
agent.actor_target.model.save_weights(os.path.join(checkpoint_path,"e{}".format(e), 'actor_target.h5'))
agent.critic_local.model.save_weights(os.path.join(checkpoint_path,"e{}".format(e), 'critic_local.h5'))
agent.critic_target.model.save_weights(os.path.join(checkpoint_path,"e{}".format(e), 'critic_target.h5'))

In [ ]:
'''
with open(f'./models/{runName}/{runName}_parameters.txt', 'w') as f:
    print(allParameters, file=f)
'''
# Saving results
with open(f'./{checkpoint_dir}/total_profits.npy', 'wb') as f:
    np.save(f, np.array(total_profit_list))
with open(f'./{checkpoint_dir}/EveryProfit_dct.json', 'w') as fp:
    json.dump(EveryProfit_dct, fp)

In [ ]:
# loading results
with open(f'./{checkpoint_dir}/total_profits.npy', 'rb') as f:
    total_profit_list = np.load(f)
with open(f'./{checkpoint_dir}/EveryProfit_dct.json', 'r') as fp:
    EveryProfit_dct = json.load(fp)

In [16]:
printTrades = False

test_data = getStockData("testdata")
l_test = len(test_data) - 1
state = getState(test_data, 0, window_size + 1)
total_profit = 0
agent.inventory = []
agent.is_eval = False
done = False
for t in range(l_test):
    action = agent.act(state)

    next_state = getState(test_data, t + 1, window_size + 1)
    reward = 0

    if action == 1:

        agent.inventory.append(test_data[t])
        if printTrades:
            print("Buy: " + formatPrice(test_data[t]))

    elif action == 2 and len(agent.inventory) > 0:
        bought_price = agent.inventory.pop(0)
        reward = max(test_data[t] - bought_price, 0)
        total_profit += test_data[t] - bought_price
        if printTrades:
            print("Sell: " + formatPrice(test_data[t]) + " | profit: " + formatPrice(test_data[t] - bought_price))

    if t == l_test - 1:
        done = True
    agent.step(action_prob, reward, next_state, done)
    state = next_state

    if done:
        print("------------------------------------------")
        print("Total Profit: " + formatPrice(total_profit))
        print("------------------------------------------")

Buy: $2819.88
Buy: $2825.81
Buy: $2851.98
Sell: $2853.09 | profit: $33.21
Buy: $2855.92
Sell: $2835.98 | profit: $10.17
Sell: $2827.37 | profit: -$24.61
Buy: $2796.34
Sell: $2805.85 | profit: -$50.07
Sell: $2808.06 | profit: $11.72
Buy: $2808.34
Buy: $2835.26
Buy: $2817.73
Buy: $2811.12
Buy: $2795.14
Buy: $2800.01
Buy: $2799.77
Buy: $2805.89
Sell: $2789.24 | profit: -$19.10
Buy: $2793.39
Sell: $2791.69 | profit: -$43.57
Buy: $2781.53
Buy: $2770.77
Buy: $2786.24
Buy: $2770.73
Buy: $2733.52
Buy: $2716.02
Buy: $2711.16
Buy: $2698.95
Buy: $2718.03
Buy: $2691.99
Buy: $2699.38
Buy: $2715.60
Buy: $2698.67
Buy: $2752.68
Buy: $2744.39
Sell: $2763.91 | profit: -$53.82
Buy: $2743.19
Buy: $2757.12
Sell: $2761.73 | profit: -$49.39
Sell: $2776.52 | profit: -$18.62
Buy: $2774.65
Buy: $2778.78
Sell: $2780.17 | profit: -$19.84
Sell: $2763.59 | profit: -$36.18
Buy: $2760.16
Buy: $2748.46
Buy: $2739.51
Buy: $2740.54
Sell: $2718.70 | profit: -$87.19
Buy: $2700.68
Buy: $2702.43
Buy: $2676.81
Buy: $2714.99
